In [1]:
from Greeks_cal import *
from get_trade_signal import *
import pandas as pd
import numpy as np
import warnings
warnings.filterwarnings("ignore")

In [2]:
# option_df
series = pd.read_csv(r".\series.csv")
series = series[series["合约系列"] != "小计"]
series["合约系列"] = series["合约系列"].apply(lambda x: x.strip())
series = series.loc[series.groupby("trade_date")["持仓量"].idxmax(), :].set_index(["trade_date", "合约系列"])

contracts = pd.read_csv(r".\all_combined_options_with_spot_price.csv")
contracts = contracts[['trade_date', 'C/P','合约系列','合约代码','开盘价','最高价','最低价','收盘价','前结算价','结算价','涨跌1','涨跌2','成交量','持仓量','持仓量变化','成交额','德尔塔','行权量']]
contracts['trade_date'] = pd.to_datetime(contracts['trade_date'], format='%Y%m%d')
contracts["合约系列"] = contracts["合约代码"].apply(lambda x: x[:6])
contracts["trade_date"] = pd.to_datetime(contracts["trade_date"])
contracts = contracts.set_index(["trade_date", "合约系列"]).loc[series.index, :].reset_index()
contracts["C/P"] = contracts["合约代码"].apply(lambda x: x[6])
contracts["trade_date"] = pd.to_datetime(contracts["trade_date"])
# contracts = contracts.groupby(["trade_date", "C/P"]).filter(lambda x: (x["成交量"] > 20000).any()) # 最小交易量1000
# contracts = contracts.set_index(["trade_date", "C/P"])
contracts = contracts.loc[contracts.groupby([contracts["trade_date"], contracts["C/P"]])["成交量"].idxmax(), :].set_index(["trade_date", "C/P"])
contracts
spot_price = pd.read_csv(r".\all_combined_options_with_spot_price.csv")

updated_contracts = calculate_greeks(contracts, series, spot_price)
updated_contracts = updated_contracts.reset_index()
updated_contracts = updated_contracts[['合约代码', 'trade_date', '收盘价', '成交量', '持仓量', 'delta', 'gamma', 'theta', 'vega', 'rho']]
option_df = updated_contracts.rename(columns={'合约代码': 'id', 'trade_date': 'time', '收盘价': 'close', '成交量': 'volume', '持仓量': 'open_interest'})
option_df.sort_values(['id', 'time'])
option_df # 行数是可用的期权的数量

id       time  close  volume  open_interest  \
0     au2004C364                     2019-12-20   2.94  1880.0          720.0   
1     au2004P308                     2019-12-20   0.60   378.0          182.0   
2     au2004C364                     2019-12-23   3.94  1678.0         1386.0   
3     au2004P308                     2019-12-23   0.64   556.0          288.0   
4     au2004C364                     2019-12-24   4.48  1504.0         1558.0   
...                              ...        ...    ...     ...            ...   
2415  au2502P600                     2024-12-13   3.54  5328.0         4008.0   
2416  au2502C632                     2024-12-16   6.70  3947.0         1693.0   
2417  au2502P600                     2024-12-16   3.98  3967.0         3093.0   
2418  au2502C632                     2024-12-17   6.16  2516.0         1805.0   
2419  au2502P600                     2024-12-17   3.96  3023.0         3398.0   

         delta     gamma      theta        vega        rho  
0     0.171227  0.009651 -10.721661   50.144120  19.111347  
1    -0.120740  0.007627  -8.444975   39.628366  14.612209  
2     0.200667  0.009740 -13.173437   54.797273  21.793449  
3    -0.134633  0.007525 -10.128853   42.332712  16.019718  
4     0.231589  0.010012 -15.251891   59.629898  24.974420  
...        ...       ...        ...         ...        ...  
2415 -0.273511  0.006855 -43.426751   93.548893  36.342424  
2416  0.471601  0.008374 -54.166157  109.573315  54.056498  
2417 -0.270473  0.006964 -43.965528   91.125503  34.439837  
2418  0.423188  0.008493 -52.020272  106.106021  47.603371  
2419 -0.307210  0.007623 -46.224375   95.231755  38.269634  

[2420 rows x 10 columns]

In [3]:
# futures_df
spot_price = pd.read_csv(r".\all_combined_options_with_spot_price.csv")
spot_price = spot_price[['dominant_contract', 'trade_date', 'dominant_contract_price']]
futures_df = spot_price.rename(columns={'dominant_contract': 'id', 'trade_date': 'time', 'dominant_contract_price': 'close'})
futures_df['time'] = pd.to_datetime(futures_df['time'].astype(str), format='%Y%m%d')
futures_df = futures_df.drop_duplicates(subset='time', keep='first').reset_index(drop=True)
futures_df = futures_df.sort_values('time')
futures_df = futures_df.reset_index(drop=True)
futures_df = futures_df[futures_df['time'] <= pd.to_datetime('2024-12-17')]
futures_df.sort_values(['id', 'time'])
futures_df

id       time   close
0     au2006 2019-12-20  338.48
1     au2006 2019-12-23  339.14
2     au2006 2019-12-24  340.92
3     au2006 2019-12-25  343.06
4     au2006 2019-12-26  343.78
...      ...        ...     ...
1205  au2502 2024-12-11  626.00
1206  au2502 2024-12-12  629.26
1207  au2502 2024-12-13  625.94
1208  au2502 2024-12-16  620.20
1209  au2502 2024-12-17  620.78

[1210 rows x 3 columns]

In [4]:
# paras
paras = pd.DataFrame({
    'range': [[-np.inf, -50], [-50, 0], [0, 50], [50, np.inf]],
    'delta': [[-0.15, 0.15], [0.4, 0.6], [0.9, 1.1], [0.4, 0.6]],
    'gamma': [[-0.15, 0.15], [-0.15, 0.15], [-0.15, 0.15], [-0.15, 0.15]],
    'theta': [[-0.15, 0.15], [-0.15, 0.15], [-0.15, 0.15], [-0.15, 0.15]],
    'vega': [[-0.15, 0.15], [-0.15, 0.15], [-0.15, 0.15], [-0.15, 0.15]],
    'rho': [[-0.15, 0.15], [-0.15, 0.15], [-0.15, 0.15], [-0.15, 0.15]]
})

paras

range          delta          gamma          theta           vega  \
0  [-inf, -50]  [-0.15, 0.15]  [-0.15, 0.15]  [-0.15, 0.15]  [-0.15, 0.15]   
1     [-50, 0]     [0.4, 0.6]  [-0.15, 0.15]  [-0.15, 0.15]  [-0.15, 0.15]   
2      [0, 50]     [0.9, 1.1]  [-0.15, 0.15]  [-0.15, 0.15]  [-0.15, 0.15]   
3    [50, inf]     [0.4, 0.6]  [-0.15, 0.15]  [-0.15, 0.15]  [-0.15, 0.15]   

             rho  
0  [-0.15, 0.15]  
1  [-0.15, 0.15]  
2  [-0.15, 0.15]  
3  [-0.15, 0.15]

In [5]:
start_time_first = pd.to_datetime('2020-01-01')
start_time_last = pd.to_datetime('2022-01-01')
# 每7天发一只产品，t一只产品存续2年
time_list = pd.date_range(start=start_time_first, end=start_time_last, freq='7D').tolist()

for start_time in time_list:
    """paras应调整为资金希腊值。设资金量为equity，策略起始日黄金价格为spot0，合约乘数为multiplier，那么每个希腊值都应乘上equity/(spot0*multiplier)。"""
    equity = 10000000
    multiplier = 1000
    spot0 = futures_df[futures_df['time'] >= start_time]['close'].iloc[0]
    paras_equity = pd.DataFrame()
    paras_equity['range'] = paras['range']
    paras_equity[['delta', 'gamma', 'theta', 'vega', 'rho']] = paras[['delta', 'gamma', 'theta', 'vega', 'rho']].apply(lambda x: x.apply(lambda y: [z * equity/(spot0*multiplier) for z in y]))

    option_df_temp = option_df[(option_df['time'] >= start_time) & (option_df['time'] < start_time + pd.DateOffset(years=2))]
    futures_df_temp = futures_df[(futures_df['time'] >= start_time) & (futures_df['time'] < start_time + pd.DateOffset(years=2))]
    # 计算
    position_option, position_futures = get_trading_signal(option_df_temp, futures_df_temp, paras_equity, equity)
    # 保存仓位表
    str_start_time = start_time.strftime('%Y%m%d')
    position_option.to_csv(f'.\\position\\option_{str_start_time}.csv')
    position_futures.to_csv(f'.\\position\\futures_{str_start_time}.csv')


Time: 2020-01-02 00:00:00
Status: Optimal
Optimal value is: -22.979999999999997
Solution is: [-8.0, 17.0, 20.0]

Time: 2020-01-03 00:00:00
Status: Optimal
Optimal value is: -21.060000000000002
Solution is: [-13.0, 13.0, 35.0]

Time: 2020-01-06 00:00:00
Status: Optimal
Optimal value is: -14.14
Solution is: [-3.0, 4.0, 33.0]

Time: 2020-01-07 00:00:00
Status: Optimal
Optimal value is: 0.0
Solution is: [0.0, 0.0, 27.0]

Time: 2020-01-08 00:00:00
Status: Optimal
Optimal value is: -16.82
Solution is: [-2.0, 7.0, 28.0]

Time: 2020-01-09 00:00:00
Status: Optimal
Optimal value is: -12.219999999999999
Solution is: [-3.0, 8.0, 33.0]

Time: 2020-01-10 00:00:00
Status: Optimal
Optimal value is: -36.80000000000001
Solution is: [-6.0, 10.0, 35.0]

Time: 2020-01-13 00:00:00
Status: Optimal
Optimal value is: 0.0
Solution is: [0.0, 0.0, 31.0]

Time: 2020-01-14 00:00:00
Status: Optimal
Optimal value is: -75.84
Solution is: [-24.0, 23.0, 21.0]

Time: 2020-01-15 00:00:00
Status: Optimal
Optimal value is:

In [6]:
start_time_first = pd.to_datetime('2020-01-01')
start_time_last = pd.to_datetime('2022-01-01')
# 每7天发一只产品，一只产品存续2年
time_list = pd.date_range(start=start_time_first, end=start_time_last, freq='7D').tolist()
time_list

[Timestamp('2020-01-01 00:00:00'),
 Timestamp('2020-01-08 00:00:00'),
 Timestamp('2020-01-15 00:00:00'),
 Timestamp('2020-01-22 00:00:00'),
 Timestamp('2020-01-29 00:00:00'),
 Timestamp('2020-02-05 00:00:00'),
 Timestamp('2020-02-12 00:00:00'),
 Timestamp('2020-02-19 00:00:00'),
 Timestamp('2020-02-26 00:00:00'),
 Timestamp('2020-03-04 00:00:00'),
 Timestamp('2020-03-11 00:00:00'),
 Timestamp('2020-03-18 00:00:00'),
 Timestamp('2020-03-25 00:00:00'),
 Timestamp('2020-04-01 00:00:00'),
 Timestamp('2020-04-08 00:00:00'),
 Timestamp('2020-04-15 00:00:00'),
 Timestamp('2020-04-22 00:00:00'),
 Timestamp('2020-04-29 00:00:00'),
 Timestamp('2020-05-06 00:00:00'),
 Timestamp('2020-05-13 00:00:00'),
 Timestamp('2020-05-20 00:00:00'),
 Timestamp('2020-05-27 00:00:00'),
 Timestamp('2020-06-03 00:00:00'),
 Timestamp('2020-06-10 00:00:00'),
 Timestamp('2020-06-17 00:00:00'),
 Timestamp('2020-06-24 00:00:00'),
 Timestamp('2020-07-01 00:00:00'),
 Timestamp('2020-07-08 00:00:00'),
 Timestamp('2020-07-